In [ ]:
import pandas as pd
import os
current_path = os.getcwd()
bug_file = os.path.join(current_path, 'data','bugs.xlsx')
regression_bugs = pd.read_excel(bug_file,sheet_name='0709合并')

# fastjson_data = regression_bugs[regression_bugs['proj.'].str.contains('fastjson', na=False)]
#
# id_data = fastjson_data['ID'].tolist()

bug_data = regression_bugs
id_data = bug_data['ID'].tolist()


from sql_manager import MySQLDatabase
db = MySQLDatabase("10.176.34.95", "root", "1235", "code_annotation2")
db.connect()


ret = pd.DataFrame(columns=['project_name','commit_hash'])
results = []
for id in id_data:
    sql = "SELECT project_name, bic as commit_hash FROM regressions_all " # WHERE project_name = 'alibaba_fastjson'
    sql += " WHERE id = " + str(id)
    print(sql)
    result_item = db.fetch_query(sql)
    results.extend(result_item)


# 如果 results 不为空，将它们转换为 DataFrame
if results:
    ret = pd.DataFrame(results, columns=['project_name', 'commit_hash'])

print(len(ret))

In [2]:
ret.head(10)
# 对 'project_name' 列中的下划线进行分割并只保留后半部分
ret['project_name'] = ret['project_name'].str.split('_').str[-1]
ret.to_pickle('../data/all_regression_bugs.pkl') # 待处理数据

JITFINE_data test.py得到280个bug的专家特征

In [1]:
import pickle
import pandas as pd

expert_features = pickle.load(open('../data/all_changes_data/metrics.pkl','rb')) # 读取数据
type(expert_features)
expert_features['is_buggy_commit'] = 1

expert_features.to_excel('../data/14-feature.xlsx') # 保存数据 #手动检查大异常

manual_features_columns = ['la', 'ld', 'nf', 'ns', 'nd', 'entropy', 'ndev',
                           'lt', 'nuc', 'age', 'exp', 'rexp', 'sexp']
expert_features[manual_features_columns] = expert_features[manual_features_columns].apply(pd.to_numeric, errors='coerce').fillna(0)
pickle.dump(expert_features, open('../data/features_reg_test.pkl', 'wb')) # 保存数据

In [2]:
import pandas as pd
print_expert = pd.read_pickle('../data/features_reg_test.pkl') # 读取数据
print(print_expert.head)

<bound method NDFrame.head of               project                             parent_hashes  \
0          cron-utils  3653781ca21217eb45d4a840867735b81b2eb21c   
1          cron-utils  02f23bb3469856154641dac64c6b90013432e085   
2          cron-utils  d6d94dfba8d9d123a5d1406a47173bc898654078   
3          cron-utils  9e807b8aa427c0a73e3f6a94a94d97cc0c49b82a   
4          cron-utils  c1777d3635deae3f2262c58c0c157c0446dd1b4a   
..                ...                                       ...   
228     consul-client  aa838f7a3c6ee6c1640dc8f4cf998176bfab46cc   
229             blade  9df2321a74bbb17f08a7c87e33eb16758cca4aed   
230           javadbf  b9f7327549971089a72bb4f36e547757529ea69c   
231             ice4j  3fe34dcb972eedda77d3abf8d4cfb9977443854a   
232  memoryfilesystem  59f70d14d8948f7efb82e89806b1e9ba38d56a11   

                                  commit_hash          author_name  \
0    ff67527e69868a2c2b05ab8a1ddcca8d8f896e44         Joze Rozanec   
1    aeaff59fbbcaf65363ac

In [3]:
print(expert_features.shape)
expert_features['commit_hash'].unique().shape

(233, 25)


(233,)

In [23]:

expert_features['fix'] = expert_features['fix'].apply(lambda x: float(bool(x)))
df = expert_features.astype({i: 'float32' for i in manual_features_columns})

In [6]:
# import os
# expert_features_example = pickle.load(open(os.path.join(os.getcwd(),'data','features_test.pkl') ,'rb'))

In [ ]:
# expert_features_example.columns == expert_features.columns

提取JITFine和smart的公共部分 changes_test 格式，格式是一个list.size =4 

In [4]:
import os 
current_path = os.getcwd()
test_buggy_commit_lines_df = pd.read_pickle(os.path.join(current_path, 'data','test_buggy_commit_lines_df.pkl'))
columns = test_buggy_commit_lines_df.columns
test_buggy_reg_lines_results = pd.DataFrame(columns=columns)
test_buggy_reg_lines_results.head(10)

Empty DataFrame
Columns: [project, file, change type, commit hash, idx, code line, label]
Index: []

In [5]:
test_buggy_commit_lines_df

project                                               file change type  \
0      ant-ivy  src/java/org/apache/ivy/util/url/BasicURLHandl...       added   
1      ant-ivy  src/java/org/apache/ivy/util/url/BasicURLHandl...       added   
2      ant-ivy  src/java/org/apache/ivy/util/url/BasicURLHandl...       added   
3      ant-ivy  src/java/org/apache/ivy/util/url/BasicURLHandl...       added   
4      ant-ivy  src/java/org/apache/ivy/util/url/BasicURLHandl...       added   
...        ...                                                ...         ...   
26660     gora  gora-solr-5/src/main/java/org/apache/gora/solr...       added   
26661     gora  gora-solr-5/src/main/java/org/apache/gora/solr...       added   
26662     gora  gora-solr-5/src/main/java/org/apache/gora/solr...       added   
26663     gora  gora-solr-5/src/main/java/org/apache/gora/solr...       added   
26664     gora  gora-solr-5/src/main/java/org/apache/gora/solr...       added   

                                    commit hash  idx  \
0      6e710a1f78a4a733020a4b2d1f07b6fe4c6684f0    0   
1      6e710a1f78a4a733020a4b2d1f07b6fe4c6684f0    1   
2      6e710a1f78a4a733020a4b2d1f07b6fe4c6684f0    2   
3      6e710a1f78a4a733020a4b2d1f07b6fe4c6684f0    3   
4      6e710a1f78a4a733020a4b2d1f07b6fe4c6684f0    4   
...                                         ...  ...   
26660  348e020e1df6c0b3a5b8c38b220746617320fb43  382   
26661  348e020e1df6c0b3a5b8c38b220746617320fb43  383   
26662  348e020e1df6c0b3a5b8c38b220746617320fb43  384   
26663  348e020e1df6c0b3a5b8c38b220746617320fb43  385   
26664  348e020e1df6c0b3a5b8c38b220746617320fb43  386   

                                               code line  label  
0                                  url = normalize(url);      1  
1                                dest = normalize(dest);      1  
2                                  src = normalize(src);      1  
3                                             throw ioe;      0  
4      URI uri = new URI(url.getProtocol(), url.getUs...      0  
...                                                  ...    ...  
26660  import org.apache.solr.common.params.CommonPar...      0  
26661  SpecificDatumWriter writer = writerMap.get(fie...      0  
26662                writerMap.put(fieldSchema, writer);      0  
26663                    public String getSchemaName() {      0  
26664                                        case UNION:      0  

[26665 rows x 7 columns]

In [6]:
# changes_test_example = pd.read_pickle(os.path.join(current_path, 'data','changes_test.pkl'))
# changes_test_example

[['...',
  ...],
 [1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0

JITFIne:
    changes_reg_test.pkl
    features_reg_test.pkl
    complete_buggy_line.pkl
JITSmat:
    test_buggy_reg_lines_results.pkl


这里开始提取JITSmart和JITFine的数据，他俩有公共部fen。首先JITFIne JITSmart的数据要包括changes_reg_test.pkl 和 features_reg_test.pkl,且是放下JITFine的数据目录下的 。 features_reg_test.pkl 已经有了所以下面提取其他的
下面的代码会生成changes_reg_test.pkl 和 JITSmart 所需要的test_buggy_reg_lines_results.pkl

In [7]:
import subprocess
import re
from pathlib import Path
import os
from utils import getDiffFromRepo
current_path = os.getcwd()
repos_data_path = os.path.join(Path(current_path).parent, 'repos')

commits = []
buggy_labels = []
msgs = []
commits_code_changes = []
changes_results = []

for index, column in expert_features.iterrows():
    project_name = column['project']
    commit_hash = column['commit_hash']
    commits.append(commit_hash)
    buggy_labels.append(1)
    msgs.append(column['commit_message'])
    project_path = os.path.join(repos_data_path, project_name)
    
    files_changes_dict= getDiffFromRepo(project_path, commit_hash)

    code_changes = {
        'added_code': set(),
        'removed_code': set()
    }
    
    added_lines = []  # 使用 set 存储 added 行
    deleted_lines = []  # 使用 set 存储 deleted 行        
    seen_lines = set() 
    
    for  file_path, changes in files_changes_dict.items():
        rowidx = 0 
        for line in changes['added_code']:
            line = line.strip().replace('\n','').replace('\t','')
            is_comments =  line.startswith('//') or line.startswith('/*') or line.startswith('*') or not line 
            if not is_comments:
                code_changes['added_code'].add(line)
                

        for line in changes['removed_code']:
            line = line.strip().replace('\n','').replace('\t','')
            is_comments =  line.startswith('//') or line.startswith('/*') or line.startswith('*') or not line 
            if not is_comments:
                code_changes['removed_code'].add(line)


    for  file_path, changes in files_changes_dict.items():
        rowidx = 0 
        for line in changes['added_code']:
            line = line.strip().replace('\n','').replace('\t','')
            is_comments =  line.startswith('//') or line.startswith('/*') or line.startswith('*') or not line 
            if not is_comments and line not in seen_lines:
                row_item = {'project': project_name, 'file': file_path, 'change type': 'added', 'commit hash': commit_hash, 'idx': rowidx, 'code line': line, 'label': 1}
                added_lines.append(row_item)
                seen_lines.add(line)
                rowidx += 1

        for line in changes['removed_code']:
            line = line.strip().replace('\n','').replace('\t','')
            is_comments =  line.startswith('//') or line.startswith('/*') or line.startswith('*') or not line 
            if not is_comments and line not in seen_lines:
                row_item = {'project': project_name, 'file': file_path, 'change type': 'deleted', 'commit hash': commit_hash, 'idx': rowidx, 'code line': line, 'label': 1}
                deleted_lines.append(row_item)
                seen_lines.add(line)
                rowidx += 1  # 每次添加后递增 rowidx            

    # 将 added 行和 deleted 行转换为 DataFrame
    added_df = pd.DataFrame(added_lines)
    deleted_df = pd.DataFrame(deleted_lines)

    # 确保 added 行在 deleted 行之前，合并 DataFrame
    test_buggy_reg_lines_results = pd.concat([test_buggy_reg_lines_results, added_df, deleted_df], ignore_index=True)

    commits_code_changes.append(code_changes)
changes_results.append(commits)
changes_results.append(buggy_labels)
changes_results.append(msgs)
changes_results.append(commits_code_changes)



In [ ]:
print(len(set(commits)))
print(test_buggy_reg_lines_results['commit hash'].unique().shape)

print(len(buggy_labels))
print(len(msgs))
print(len(commits_code_changes))
print(len(changes_results))
print(type(changes_results))   
print(type(changes_results[0]))
print(type(changes_results[0][1]))
print(len(set(commits)))

In [ ]:
len(changes_results[3])

In [17]:
pickle.dump(changes_results, open('../data/changes_reg_test.pkl', 'wb')) 

In [ ]:
import pandas as pd

# 获取唯一的 commit hash 列表
test_commit_hashes = set(test_buggy_reg_lines_results['commit hash'].unique())
expert_commit_hashes = set(expert_features['commit_hash'].unique())

# 找出 expert_features 中存在，但 test_buggy_reg_lines_results 中不存在的 commit_hash
missing_commit_hashes = expert_commit_hashes - test_commit_hashes

print(f"Missing commit hashes: {missing_commit_hashes}")

In [ ]:
# 获取 'commit hash' 列的不重复数量
unique_commit_hash_count = test_buggy_reg_lines_results['commit hash'].nunique()
print(unique_commit_hash_count)

for index,column in test_buggy_reg_lines_results.iterrows():
    commit_hash = column['commit hash']
    project_name = column['project']
    file_path = column['file']
    change_type = column['change type']
    idx = column['idx']
    code_line = column['code line']
    label = column['label']
    print(f'commit hash: {commit_hash}, project: {project_name}, file: {file_path}, change type: {change_type}, idx: {idx}, code line: {code_line}, label: {label}')

In [7]:
test_buggy_reg_lines_results.to_pickle('../data/test_buggy_reg_lines_results.pkl')

到此为止 JITSmart的数据结束。 JITFIne 还缺  complete_buggy_line.pkl
数据生成在JITFine_data/data/test.py

到此为止JIT FIne 和smart 已经结束

In [ ]:
pd.read_pickle('../data/test_buggy_reg_lines_results.pkl')

In [ ]:
# # JITFine 
# jitfine_data = pickle.load(open(os.path.join(current_path, 'data','changes_complete_buggy_line_level.pkl'),'rb'))
# jitfine_data

In [ ]:
# jitfine_data.columns
# jitfine_reg_data = pickle.load(open('/Users/sxz/Documents/coding/project/empirical-study/JITFine_data/data/complete_buggy_line.pkl','rb'))


 DeeperJIT 和 CC2vec

In [ ]:
import pickle
import os
current_path = os.getcwd()
# deeperjit_features_example = pickle.load(open(os.path.join(current_path, 'data','deeperjit-features_test.pkl'),'rb'))
# print(len(deeperjit_features_example))
# print(type(deeperjit_features_example[0]))
# print(type(deeperjit_features_example[0][0]))

In [ ]:
# print(type(deeperjit_features_example[1]))
# print(type(deeperjit_features_example[1][0]))
# print(type(deeperjit_features_example[2]))
# print(type(deeperjit_features_example[2][0]))
# print(type(deeperjit_features_example[3]))
# print(type(deeperjit_features_example[3][0]))
# print(type(deeperjit_features_example[3][0][0]))

In [ ]:
# import json
# print(deeperjit_features_example[3][1])
# json_str = json.dumps(deeperjit_features_example, ensure_ascii=False, indent=4)
# print(json_str)

In [ ]:
# deeperjit_projects_test_example = pickle.load(open(os.path.join(current_path, 'data','deeperjit-projects_test.pkl'),'rb'))
# print(type(deeperjit_projects_test_example))


In [13]:
def split_sentence(sentence):
    sentence = sentence.replace('.', ' . ').replace('_', ' ').replace('@', ' @ ')\
        .replace('-', ' - ').replace('~', ' ~ ').replace('%', ' % ').replace('^', ' ^ ')\
        .replace('&', ' & ').replace('*', ' * ').replace('(', ' ( ').replace(')', ' ) ')\
        .replace('+', ' + ').replace('=', ' = ').replace('{', ' { ').replace('}', ' } ')\
        .replace('|', ' | ').replace('\\', ' \ ').replace('[', ' [ ').replace(']', ' ] ')\
        .replace(':', ' : ').replace(';', ' ; ').replace(',', ' , ').replace('<', ' < ')\
        .replace('>', ' > ').replace('?', ' ? ').replace('/', ' / ')
    sentence = ' '.join(sentence.split())
    return sentence
import random

deeperjit_changes_results = []
deeperjit_changes_results.append(changes_results[0])
deeperjit_changes_results.append(changes_results[1])
deeperjit_changes_results.append(changes_results[2])
deeperjit_changes_list = []

codes, deepjit_codes, deepjit_raw_codes = [], [], []

for index, column in expert_features.iterrows():
    project_name = column['project']
    commit_hash = column['commit_hash']

    project_path = os.path.join(repos_data_path, project_name)
    
    files_changes_dict= getDiffFromRepo(project_path, commit_hash)
    
    format_code = []
    files_code = []
    raw_code = []

    for  file_path, changes in files_changes_dict.items():

        added_code, removed_code, file_codes = [], [], []

        for line in changes['removed_code']:
       
            remove_code = line.strip()
            remove_code = ' '.join(split_sentence(remove_code).split())
            remove_code = ' '.join(remove_code.split(' '))
      
            removed_code.append(remove_code)
            file_codes.append((line, remove_code))
            if len(removed_code) > 10: break

        for line in changes['added_code']:
            # if len(diff['b'][line]['code'].split()) > 3:
            add_code = line.strip()
            add_code = ' '.join(split_sentence(add_code).split())
            add_code = ' '.join(add_code.split(' '))
            # add_code = 'added _ code removed _ code'
            added_code.append(add_code)
            file_codes.append((line, add_code))
            if len(added_code) > 10: break

        file_codes.sort(key=lambda x: x[0])
        raw_code.extend([code[1] for code in file_codes])
        raw_code = raw_code[:10]
        format_code.append("added _ code removed _ code")
        files_code.append({'added_code': added_code, 'removed_code': removed_code})
            # shuffle(code)
        if len(format_code) == 10: break

    deepjit_codes.append(format_code)
    deepjit_raw_codes.append(raw_code)
    codes.append(files_code)

deeperjit_changes_results=[changes_results[0], changes_results[1], changes_results[2], deepjit_raw_codes]
cc2Vec_changes_results = [changes_results[0], changes_results[1], changes_results[2], codes]


print(deeperjit_changes_results[3][0])


['expression . accept ( new ValidationFieldExpressionVisitor ( constraints ) ) ;', 'expression . accept ( new ValidationFieldExpressionVisitor ( constraints , definition . isStrictRanges ( ) ) ) ;', 'new ValidationFieldExpressionVisitor ( getCronDefinition ( ) . getFieldDefinition ( fieldName ) . getConstraints ( ) )', 'new ValidationFieldExpressionVisitor ( getCronDefinition ( ) . getFieldDefinition ( fieldName ) . getConstraints ( ) , cronDefinition . isStrictRanges ( ) )', '*', '* @ return true if should be enforced , false otherwise .', "* If ranges for field values should be strictly enforced ( 'from' greater than 'to' ) .", '* /', 'final boolean strictRanges , final boolean matchDayOfWeekAndDayOfMonth ) {', 'private final boolean strictRanges ;']


In [14]:
pickle.dump(deeperjit_changes_results, open('../data/deeperjit_changes_test.pkl', 'wb'))
pickle.dump(cc2Vec_changes_results, open('../data/cc2Vec_changes_test.pkl', 'wb'))

In [ ]:
# 尝试不同种子以找到 1 比率最高的种子
best_seed = None
best_ratio = 0

# 尝试不同种子
for seed in range(10000):
    random.seed(seed)
    random_list = [random.choice([0, 1]) for _ in range(280)]
    ratio_of_ones = random_list.count(1) / len(random_list)
    
    # 更新最佳种子
    if ratio_of_ones > best_ratio:
        best_ratio = ratio_of_ones
        best_seed = seed

best_seed, best_ratio

CC2Vec

In [8]:
#check data format

import pickle
cc2vec_features_example =  pickle.load(open('data/cc2vec_features_test.pkl','rb'))
print(len(cc2vec_features_example))
for i in range(len(cc2vec_features_example)):
    print(type(cc2vec_features_example[i]))
    print(len(cc2vec_features_example[i]))
    print(type(cc2vec_features_example[i][0]))

print(cc2vec_features_example[3][100])

4
<class 'list'>
5480
<class 'str'>
<class 'list'>
5480
<class 'int'>
<class 'list'>
5480
<class 'str'>
<class 'list'>
5480
<class 'list'>
[{'added_code': ['Message . verbose ( "Parent module doesn\'t exist on the filesystem : " + file . getAbsolutePath ( ) ) ;'], 'removed_code': []}]


files_changes_dict

现在我们已经有了 四个模型的数据了，还差deeper 只需要专家特征 Lapredict，只需要专家特征 JITLine 和JITFine的一样